In [2]:
!pip install git+https://github.com/kernelmachine/allennlp.git@4ae123d2c3bfb1ea3ce7362cb6c5bca3d094ffa7
!pip install transformers==2.6.0
!pip install pytorch-transformers==1.2.0
!git clone https://github.com/allenai/dont-stop-pretraining

  Cloning https://github.com/kernelmachine/allennlp.git (to revision 4ae123d2c3bfb1ea3ce7362cb6c5bca3d094ffa7) to /tmp/pip-req-build-l83c5pe7
  Running command git clone -q https://github.com/kernelmachine/allennlp.git /tmp/pip-req-build-l83c5pe7
  Running command git checkout -q 4ae123d2c3bfb1ea3ce7362cb6c5bca3d094ffa7
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 5.3MB 7.0MB/s 
     |████████████████████████████████| 71kB 10.6MB/s 
     |████████████████████████████████| 133kB 31.0MB/s 
     |████████████████████████████████| 266kB 56.8MB/s 
     |████████████████████████████████| 51kB 7.5MB/s 
     |████████████████████████████████| 245kB 42.6MB/s 
     |████████████████████████████████| 133kB 40.0MB/s 
     |████████████████████████████████| 317kB 44.6MB/s 
     |████████████████████████████████| 163kB 35.5MB/s 
     |████████████████████████████████| 51kB 7.4MB/s

In [3]:
%cd /content/dont-stop-pretraining
!pwd

/content/dont-stop-pretraining
/content/dont-stop-pretraining


In [1]:
import torch
if torch.cuda.is_available():
  device = torch.device("cuda")
else:
  device = torch.device("cpu")
print(device)

!nvidia-smi

cuda
Sat Nov 14 01:55:59 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 455.32.00    Driver Version: 418.67       CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   35C    P0    24W / 300W |     10MiB / 16130MiB |      0%      Default |
|                               |                      |                 ERR! |
+-------------------------------+----------------------+----------------------+
                                                                               
+--

In [ ]:
!curl -Lo train.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/chemprot/train.jsonl
!curl -Lo dev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/chemprot/dev.jsonl
!curl -Lo test.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/chemprot/test.jsonl

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 1094k  100 1094k    0     0  4277k      0 --:--:-- --:--:-- --:--:-- 4277k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  662k  100  662k    0     0  3068k      0 --:--:-- --:--:-- --:--:-- 3068k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  937k  100  937k    0     0  4712k      0 --:--:-- --:--:-- --:--:-- 4712k


In [ ]:
!curl -Lo hyptrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/hyperpartisan_news/train.jsonl
!curl -Lo hypdev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/hyperpartisan_news/dev.jsonl
!curl -Lo hyptest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/hyperpartisan_news/test.jsonl

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 1708k  100 1708k    0     0   990k      0  0:00:01  0:00:01 --:--:--  990k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  197k  100  197k    0     0   155k      0  0:00:01  0:00:01 --:--:--  155k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  241k  100  241k    0     0   171k      0  0:00:01  0:00:01 --:--:--  171k


In [ ]:
import pandas as pd
import json
data = []
with open("hyptrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("hyptrain.txt", header=False, index=False)
data = []
with open("hypdev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("hypdev.txt", header=False, index=False)

In [ ]:
!ls

ADAPTIVE_PRETRAINING.md  environment.yml  hyptrain.jsonl  scatter.pdf
DATA_SELECTION.md	 hypdev.jsonl	  hyptrain.txt	  scripts
dont_stop_pretraining	 hypdev.txt	  mlm_study	  search_space
environments		 hyptest.jsonl	  README.md	  training_config


In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file hyptrain.txt \
                --line_by_line \
                --output_dir roberta_tapt3 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 8  \
                --model_name_or_path roberta-base \
                --eval_data_file hypdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  28% 18/65 [00:06<00:16,  2.88it/s]
Iteration:  29% 19/65 [00:06<00:15,  2.89it/s]
Iteration:  31% 20/65 [00:06<00:15,  2.90it/s]
Iteration:  32% 21/65 [00:07<00:15,  2.91it/s]
Iteration:  34% 22/65 [00:07<00:14,  2.92it/s]
Iteration:  35% 23/65 [00:07<00:14,  2.92it/s]
Iteration:  37% 24/65 [00:08<00:14,  2.81it/s]
Iteration:  38% 25/65 [00:08<00:14,  2.85it/s]
Iteration:  40% 26/65 [00:08<00:13,  2.88it/s]
Iteration:  42% 27/65 [00:09<00:13,  2.90it/s]
Iteration:  43% 28/65 [00:09<00:12,  2.92it/s]
Iteration:  45% 29/65 [00:09<00:12,  2.93it/s]
Iteration:  46% 30/65 [00:10<00:11,  2.94it/s]
Iteration:  48% 31/65 [00:10<00:11,  2.94it/s]
Iteration:  49% 32/65 [00:11<00:11,  2.80it/s]
Iteration:  51% 33/65 [00:11<00:11,  2.84it/s]
Iteration:  52% 34/65 [00:11<00:10,  2.86it/s]
Iteration:  54% 35/65 [00:12<00:10,  2.88it/s]
Iteration:  55% 36/65 [00:12<00:10,  2.90it/s]
Iteration:  57% 37/65 [00:12<00:09,  2.91it/s]
Iteration

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/hyp_tapt_03 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset hyperpartisan_news \
        --model roberta_tapt3 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 14:06:24,546 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 14:06:24,965 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 14:06:24,968 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 14:06:25,434 - INFO - allennlp.common.params - random_seed = 746981
2020-11-10 14:06:25,434 - INFO - allennlp.common.params - numpy_seed = 746981
2020-11-10 14:06:25,434 - INFO - allennlp.common.params - pytorch_seed = 746981
2020-11-10 14:06:25,441 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 14:06:25,443 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 14:06:25,443 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!curl -Lo chemtrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/chemprot/train.jsonl
!curl -Lo chemdev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/chemprot/dev.jsonl
!curl -Lo chemtest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/chemprot/test.jsonl
data = []
with open("chemtrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("chemtrain.txt", header=False, index=False)
data = []
with open("chemdev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("chemdev.txt", header=False, index=False)

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 1094k  100 1094k    0     0   578k      0  0:00:01  0:00:01 --:--:--  577k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  662k  100  662k    0     0   432k      0  0:00:01  0:00:01 --:--:--  431k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  937k  100  937k    0     0   597k      0  0:00:01  0:00:01 --:--:--  597k


In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file chemtrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_chem_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 8  \
                --model_name_or_path roberta-base \
                --eval_data_file chemdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  49% 258/522 [00:21<00:19, 13.23it/s]
Iteration:  50% 260/522 [00:21<00:19, 13.12it/s]
Iteration:  50% 262/522 [00:21<00:19, 13.51it/s]
Iteration:  51% 264/522 [00:21<00:21, 11.98it/s]
Iteration:  51% 266/522 [00:21<00:24, 10.61it/s]
Iteration:  51% 268/522 [00:22<00:22, 11.12it/s]
Iteration:  52% 270/522 [00:22<00:20, 12.35it/s]
Iteration:  52% 272/522 [00:22<00:21, 11.63it/s]
Iteration:  52% 274/522 [00:22<00:19, 12.62it/s]
Iteration:  53% 276/522 [00:22<00:18, 13.36it/s]
Iteration:  53% 278/522 [00:22<00:18, 13.45it/s]
Iteration:  54% 280/522 [00:23<00:19, 12.18it/s]
Iteration:  54% 282/522 [00:23<00:19, 12.61it/s]
Iteration:  54% 284/522 [00:23<00:18, 12.92it/s]
Iteration:  55% 286/522 [00:23<00:21, 11.19it/s]
Iteration:  55% 288/522 [00:23<00:22, 10.55it/s]
Iteration:  56% 290/522 [00:24<00:23,  9.82it/s]
Iteration:  56% 292/522 [00:24<00:23,  9.96it/s]
Iteration:  56% 294/522 [00:24<00:20, 11.24it/s]
Iteration:  57% 29

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/chem_tapt_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset chemprot \
        --model roberta_tapt_chem_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 16:06:18,713 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 16:06:19,450 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 16:06:19,453 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 16:06:20,029 - INFO - allennlp.common.params - random_seed = 222455
2020-11-10 16:06:20,029 - INFO - allennlp.common.params - numpy_seed = 222455
2020-11-10 16:06:20,029 - INFO - allennlp.common.params - pytorch_seed = 222455
2020-11-10 16:06:20,054 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 16:06:20,055 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 16:06:20,055 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!curl -Lo cittrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/citation_intent/train.jsonl
!curl -Lo citdev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/citation_intent/dev.jsonl
!curl -Lo citest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/citation_intent/test.jsonl
data = []
with open("cittrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("cittrain.txt", header=False, index=False)
data = []
with open("citdev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("citdev.txt", header=False, index=False)

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  454k  100  454k    0     0   299k      0  0:00:01  0:00:01 --:--:--  298k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 30138  100 30138    0     0  34641      0 --:--:-- --:--:-- --:--:-- 34601
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 38637  100 38637    0     0  45455      0 --:--:-- --:--:-- --:--:-- 45401


In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file cittrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_cit_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 8  \
                --model_name_or_path roberta-base \
                --eval_data_file citdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  61% 128/211 [00:10<00:06, 12.35it/s]
Iteration:  62% 130/211 [00:10<00:06, 12.54it/s]
Iteration:  63% 132/211 [00:10<00:06, 12.57it/s]
Iteration:  64% 134/211 [00:10<00:05, 13.41it/s]
Iteration:  64% 136/211 [00:10<00:05, 13.04it/s]
Iteration:  65% 138/211 [00:10<00:05, 13.42it/s]
Iteration:  66% 140/211 [00:11<00:05, 13.41it/s]
Iteration:  67% 142/211 [00:11<00:04, 14.20it/s]
Iteration:  68% 144/211 [00:11<00:05, 13.12it/s]
Iteration:  69% 146/211 [00:11<00:04, 14.59it/s]
Iteration:  70% 148/211 [00:11<00:04, 14.19it/s]
Iteration:  71% 150/211 [00:11<00:04, 13.91it/s]
Iteration:  72% 152/211 [00:12<00:04, 12.24it/s]
Iteration:  73% 154/211 [00:12<00:04, 13.45it/s]
Iteration:  74% 156/211 [00:12<00:04, 13.29it/s]
Iteration:  75% 158/211 [00:12<00:04, 12.70it/s]
Iteration:  76% 160/211 [00:12<00:04, 12.65it/s]
Iteration:  77% 162/211 [00:12<00:03, 13.73it/s]
Iteration:  78% 164/211 [00:12<00:03, 13.84it/s]
Iteration:  79% 16

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/cit_tapt_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset citation_intent \
        --model roberta_tapt_cit_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 16:52:04,055 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 16:52:04,690 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 16:52:04,693 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 16:52:05,191 - INFO - allennlp.common.params - random_seed = 462804
2020-11-10 16:52:05,191 - INFO - allennlp.common.params - numpy_seed = 462804
2020-11-10 16:52:05,192 - INFO - allennlp.common.params - pytorch_seed = 462804
2020-11-10 16:52:05,200 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 16:52:05,201 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 16:52:05,202 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
import json
import pandas as pd
!curl -Lo sciietrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/sciie/train.jsonl
!curl -Lo sciiedev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/sciie/dev.jsonl
!curl -Lo sciieest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/sciie/test.jsonl
data = []
with open("sciietrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("sciietrain.txt", header=False, index=False)
data = []
with open("sciiedev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("sciiedev.txt", header=False, index=False)

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  804k  100  804k    0     0   527k      0  0:00:01  0:00:01 --:--:--  527k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  115k  100  115k    0     0  98875      0  0:00:01  0:00:01 --:--:-- 98875
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  243k  100  243k    0     0   180k      0  0:00:01  0:00:01 --:--:--  180k


In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file sciietrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_sciie_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 8  \
                --model_name_or_path roberta-base \
                --eval_data_file sciiedev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  96% 385/403 [00:23<00:01, 15.90it/s]
Iteration:  96% 387/403 [00:23<00:00, 16.24it/s]
Iteration:  97% 389/403 [00:23<00:00, 16.53it/s]
Iteration:  97% 391/403 [00:23<00:00, 15.79it/s]
Iteration:  98% 393/403 [00:23<00:00, 14.31it/s]
Iteration:  98% 395/403 [00:23<00:00, 15.00it/s]
Iteration:  99% 398/403 [00:23<00:00, 16.53it/s]11/10/2020 17:34:07 - INFO - __main__ -   Creating features from dataset file at sciiedev.txt
11/10/2020 17:34:07 - INFO - __main__ -   ***** Running evaluation  *****
11/10/2020 17:34:07 - INFO - __main__ -     Num examples = 455
11/10/2020 17:34:07 - INFO - __main__ -     Batch size = 4


Evaluating:   0% 0/114 [00:00<?, ?it/s]

Evaluating:   7% 8/114 [00:00<00:01, 74.29it/s]

Evaluating:  14% 16/114 [00:00<00:01, 72.77it/s]

Evaluating:  21% 24/114 [00:00<00:01, 73.18it/s]

Evaluating:  27% 31/114 [00:00<00:01, 71.87it/s]

Evaluating:  33% 38/114 [00:00<00:01, 71.15it/s]

Evaluating:  40% 46/114 [

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/sciie_tapt_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset sciie \
        --model roberta_tapt_sciie_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 17:43:48,171 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 17:43:48,863 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 17:43:48,867 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 17:43:49,778 - INFO - allennlp.common.params - random_seed = 599026
2020-11-10 17:43:49,778 - INFO - allennlp.common.params - numpy_seed = 599026
2020-11-10 17:43:49,778 - INFO - allennlp.common.params - pytorch_seed = 599026
2020-11-10 17:43:49,797 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 17:43:49,798 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 17:43:49,798 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file sciietrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_sciie_02 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file sciiedev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  12% 47/403 [00:02<00:20, 17.15it/s]
Iteration:  12% 49/403 [00:02<00:21, 16.14it/s]
Iteration:  13% 51/403 [00:03<00:21, 16.50it/s]
Iteration:  13% 53/403 [00:03<00:20, 17.22it/s]
Iteration:  14% 55/403 [00:03<00:21, 16.13it/s]
Iteration:  14% 57/403 [00:03<00:20, 16.93it/s]
Iteration:  15% 60/403 [00:03<00:19, 17.50it/s]
Iteration:  15% 62/403 [00:03<00:18, 18.04it/s]
Iteration:  16% 64/403 [00:03<00:21, 15.74it/s]
Iteration:  16% 66/403 [00:03<00:20, 16.60it/s]
Iteration:  17% 68/403 [00:04<00:19, 16.83it/s]
Iteration:  17% 70/403 [00:04<00:20, 16.01it/s]
Iteration:  18% 72/403 [00:04<00:20, 16.53it/s]
Iteration:  18% 74/403 [00:04<00:19, 16.86it/s]
Iteration:  19% 76/403 [00:04<00:19, 17.08it/s]
Iteration:  19% 78/403 [00:04<00:18, 17.17it/s]
Iteration:  20% 80/403 [00:04<00:22, 14.11it/s]
Iteration:  20% 82/403 [00:04<00:21, 14.86it/s]
Iteration:  21% 85/403 [00:05<00:19, 16.00it/s]
Iteration:  22% 87/403 [00:05<00:18, 

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/sciie_tapt_02 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset sciie \
        --model roberta_tapt_sciie_02 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 18:39:17,931 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 18:39:18,590 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 18:39:18,594 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 18:39:19,444 - INFO - allennlp.common.params - random_seed = 191123
2020-11-10 18:39:19,444 - INFO - allennlp.common.params - numpy_seed = 191123
2020-11-10 18:39:19,444 - INFO - allennlp.common.params - pytorch_seed = 191123
2020-11-10 18:39:19,458 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 18:39:19,459 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 18:39:19,460 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file hyptrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_hyp_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file hypdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  32% 21/65 [00:07<00:14,  2.94it/s]
Iteration:  34% 22/65 [00:07<00:14,  2.95it/s]
Iteration:  35% 23/65 [00:07<00:14,  2.95it/s]
Iteration:  37% 24/65 [00:08<00:13,  2.96it/s]
Iteration:  38% 25/65 [00:08<00:13,  2.96it/s]
Iteration:  40% 26/65 [00:08<00:13,  2.97it/s]
Iteration:  42% 27/65 [00:09<00:12,  2.97it/s]
Iteration:  43% 28/65 [00:09<00:12,  2.96it/s]
Iteration:  45% 29/65 [00:09<00:12,  2.96it/s]
Iteration:  46% 30/65 [00:10<00:11,  2.96it/s]
Iteration:  48% 31/65 [00:10<00:11,  2.96it/s]
Iteration:  49% 32/65 [00:10<00:11,  2.86it/s]
Iteration:  51% 33/65 [00:11<00:11,  2.89it/s]
Iteration:  52% 34/65 [00:11<00:10,  2.92it/s]
Iteration:  54% 35/65 [00:11<00:10,  2.93it/s]
Iteration:  55% 36/65 [00:12<00:09,  2.94it/s]
Iteration:  57% 37/65 [00:12<00:09,  2.95it/s]
Iteration:  58% 38/65 [00:12<00:09,  2.94it/s]
Iteration:  60% 39/65 [00:13<00:08,  2.95it/s]
Iteration:  62% 40/65 [00:13<00:08,  2.95it/s]
Iteration

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/hyp_tapt_04 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset hyperpartisan_news \
        --model roberta_tapt_hyp_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 20:13:05,077 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 20:13:05,531 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 20:13:05,534 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 20:13:05,998 - INFO - allennlp.common.params - random_seed = 647809
2020-11-10 20:13:05,998 - INFO - allennlp.common.params - numpy_seed = 647809
2020-11-10 20:13:05,998 - INFO - allennlp.common.params - pytorch_seed = 647809
2020-11-10 20:13:06,005 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 20:13:06,007 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 20:13:06,007 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file chemtrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_chem_02 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file chemdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Evaluating:  51% 311/607 [00:04<00:05, 57.38it/s]

Evaluating:  52% 317/607 [00:04<00:05, 57.13it/s]

Evaluating:  53% 324/607 [00:05<00:04, 59.50it/s]

Evaluating:  54% 330/607 [00:05<00:04, 58.16it/s]

Evaluating:  56% 337/607 [00:05<00:04, 60.98it/s]

Evaluating:  57% 344/607 [00:05<00:04, 61.42it/s]

Evaluating:  58% 351/607 [00:05<00:04, 63.32it/s]

Evaluating:  59% 359/607 [00:05<00:03, 65.64it/s]

Evaluating:  60% 366/607 [00:05<00:03, 65.67it/s]

Evaluating:  62% 374/607 [00:05<00:03, 67.44it/s]

Evaluating:  63% 381/607 [00:05<00:03, 67.35it/s]

Evaluating:  64% 389/607 [00:06<00:03, 68.84it/s]

Evaluating:  65% 396/607 [00:06<00:03, 68.45it/s]

Evaluating:  66% 403/607 [00:06<00:03, 65.35it/s]

Evaluating:  68% 410/607 [00:06<00:02, 66.68it/s]

Evaluating:  69% 418/607 [00:06<00:02, 68.02it/s]

Evaluating:  70% 425/607 [00:06<00:02, 65.94it/s]

Evaluating:  71% 432/607 [00:06<00:02, 66.53it/s]

Evaluating:  72% 439/607 [00:06

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/chem_tapt_02 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset chemprot \
        --model roberta_tapt_chem_02 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 21:39:19,420 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 21:39:20,114 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 21:39:20,118 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 21:39:20,760 - INFO - allennlp.common.params - random_seed = 540207
2020-11-10 21:39:20,760 - INFO - allennlp.common.params - numpy_seed = 540207
2020-11-10 21:39:20,760 - INFO - allennlp.common.params - pytorch_seed = 540207
2020-11-10 21:39:20,768 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 21:39:20,770 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 21:39:20,770 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file cittrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_cit_02 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file citdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration: 100% 211/211 [00:15<00:00, 13.39it/s]
Epoch:  57% 57/100 [15:28<11:31, 16.07s/it]
Iteration:   0% 0/211 [00:00<?, ?it/s]
Iteration:   1% 2/211 [00:00<00:11, 18.08it/s]
Iteration:   2% 4/211 [00:00<00:13, 15.75it/s]
Iteration:   3% 6/211 [00:00<00:13, 14.93it/s]
Iteration:   4% 8/211 [00:00<00:13, 14.76it/s]
Iteration:   5% 10/211 [00:00<00:12, 15.62it/s]
Iteration:   6% 12/211 [00:00<00:13, 14.92it/s]
Iteration:   7% 14/211 [00:00<00:12, 15.49it/s]
Iteration:   8% 16/211 [00:01<00:15, 12.46it/s]
Iteration:   9% 18/211 [00:01<00:15, 12.80it/s]
Iteration:   9% 20/211 [00:01<00:15, 12.65it/s]
Iteration:  10% 22/211 [00:01<00:15, 12.18it/s]
Iteration:  11% 24/211 [00:01<00:14, 13.10it/s]
Iteration:  12% 26/211 [00:01<00:13, 13.28it/s]
Iteration:  13% 28/211 [00:02<00:13, 13.46it/s]
Iteration:  14% 30/211 [00:02<00:13, 13.50it/s]
Iteration:  15% 32/211 [00:02<00:14, 12.26it/s]
Iteration:  16% 34/211 [00:02<00:14, 12.24it/s]
Itera

In [ ]:
!ls

ADAPTIVE_PRETRAINING.md  dont_stop_pretraining	roberta_tapt_cit_02
chemdev.jsonl		 environments		runs
chemdev.txt		 environment.yml	scatter.pdf
chemtest.jsonl		 hypdev.jsonl		sciiedev.jsonl
chemtrain.jsonl		 hypdev.txt		sciiedev.txt
chemtrain.txt		 hyptest.jsonl		sciieest.jsonl
citdev.jsonl		 hyptrain.jsonl		sciietrain.jsonl
citdev.txt		 hyptrain.txt		sciietrain.txt
citest.jsonl		 mlm_study		scripts
cittrain.jsonl		 model_logs		search_space
cittrain.txt		 README.md		training_config
DATA_SELECTION.md	 roberta_tapt_chem_02


In [ ]:
rm -rf roberta_tapt3

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/cit_tapt_02 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset citation_intent \
        --model roberta_tapt_cit_02 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-10 23:11:56,054 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 23:11:56,502 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 23:11:56,505 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-10 23:11:56,983 - INFO - allennlp.common.params - random_seed = 158269
2020-11-10 23:11:56,983 - INFO - allennlp.common.params - numpy_seed = 158269
2020-11-10 23:11:56,983 - INFO - allennlp.common.params - pytorch_seed = 158269
2020-11-10 23:11:56,990 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-10 23:11:56,992 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-10 23:11:56,992 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [9]:
!curl -Lo imdbtrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/imdb/train.jsonl
!curl -Lo imdbdev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/imdb/dev.jsonl
!curl -Lo imdbtest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/imdb/test.jsonl

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 25.6M  100 25.6M    0     0  9622k      0  0:00:02  0:00:02 --:--:-- 9622k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 6651k  100 6651k    0     0  3572k      0  0:00:01  0:00:01 --:--:-- 3570k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 31.4M  100 31.4M    0     0  10.2M      0  0:00:03  0:00:03 --:--:-- 10.2M


In [ ]:
import json
import pandas as pd
data = []
with open("imdbtrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("imdbtrain.txt", header=False, index=False)
data = []
with open("imdbdev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("imdbdev.txt", header=False, index=False)

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file imdbtrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_imdb_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file imdbdev.txt \
                --do_eval \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 500

Streaming output truncated to the last 5000 lines.
Iteration:  68% 1740/2571 [09:05<04:09,  3.33it/s]
Iteration:  68% 1741/2571 [09:05<03:52,  3.57it/s]
Iteration:  68% 1742/2571 [09:05<04:06,  3.37it/s]
Iteration:  68% 1743/2571 [09:06<04:16,  3.23it/s]
Iteration:  68% 1744/2571 [09:06<04:33,  3.02it/s]
Iteration:  68% 1745/2571 [09:06<04:35,  3.00it/s]
Iteration:  68% 1746/2571 [09:07<04:35,  2.99it/s]
Iteration:  68% 1747/2571 [09:07<04:36,  2.98it/s]
Iteration:  68% 1748/2571 [09:07<03:58,  3.45it/s]
Iteration:  68% 1749/2571 [09:08<03:46,  3.63it/s]
Iteration:  68% 1750/2571 [09:08<04:00,  3.41it/s]
Iteration:  68% 1751/2571 [09:08<04:11,  3.26it/s]
Iteration:  68% 1752/2571 [09:08<03:56,  3.47it/s]
Iteration:  68% 1753/2571 [09:09<04:07,  3.30it/s]
Iteration:  68% 1754/2571 [09:09<03:42,  3.67it/s]
Iteration:  68% 1755/2571 [09:09<03:57,  3.44it/s]
Iteration:  68% 1756/2571 [09:10<04:08,  3.29it/s]
Iteration:  68% 1757/2571 [09:10<04:15,  3.19it/s]
Iteration:  68% 1758/2571 [09:1

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/imdb_tapt_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset imdb \
        --model roberta_tapt_imdb_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

In [ ]:
!curl -Lo amazontrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/amazon/train.jsonl
!curl -Lo amazondev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/amazon/dev.jsonl
!curl -Lo amazontest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/amazon/test.jsonl
data = []
with open("amazontrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("amazontrain.txt", header=False, index=False)
data = []
with open("amazondev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("amazondev.txt", header=False, index=False)

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file amazontrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_amazon_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file amazondev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/amazon_tapt_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset amazon \
        --model roberta_tapt_amazon_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

In [ ]:
!curl -Lo agtrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/ag/train.jsonl
!curl -Lo agdev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/ag/dev.jsonl
!curl -Lo agtest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/ag/test.jsonl
data = []
with open("agtrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("agtrain.txt", header=False, index=False)
data = []
with open("agdev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("agdev.txt", header=False, index=False)

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file agtrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_ag_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file agdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/ag_tapt_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset ag \
        --model roberta_tapt_ag_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

In [ ]:
!curl -Lo rcttrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/rct-20k/train.jsonl
!curl -Lo rctdev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/rct-20k/dev.jsonl
!curl -Lo rcttest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/rct-20k/test.jsonl
data = []
with open("rcttrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("rcttrain.txt", header=False, index=False)
data = []
with open("rctdev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("rctdev.txt", header=False, index=False)

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file rcttrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_rct_01 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 16  \
                --model_name_or_path roberta-base \
                --eval_data_file rctdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/rct_tapt_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI \
        --dataset rct \
        --model roberta_tapt_rct_01 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

In [4]:
!rm environments/hyperparameters.py

In [5]:
%%writefile environments/hyperparameters.py
ROBERTA_CLASSIFIER_SMALL = {
    "LEARNING_RATE": 2e-5,
    "DROPOUT": 0.1,
    "ENCODER": "CLS",
    "NUM_FEEDFORWARD_LAYERS": 1,
    "FEEDFORWARD_WIDTH_MULTIPLIER": 1,
    "EMBEDDING": "ROBERTA",
    "NUM_EPOCHS": 10,
    "PATIENCE": 3,
    "LR_SCHEDULE": 0,
    "GRAD_ACC_BATCH_SIZE": 16,
    "BATCH_SIZE": 16,
}

ROBERTA_CLASSIFIER_MINI = {
    "LEARNING_RATE": 2e-5,
    "DROPOUT": 0.1,
    "ENCODER": "CLS",
    "NUM_FEEDFORWARD_LAYERS": 1,
    "FEEDFORWARD_WIDTH_MULTIPLIER": 1,
    "EMBEDDING": "ROBERTA",
    "NUM_EPOCHS": 10,
    "PATIENCE": 3,
    "LR_SCHEDULE": 0,
    "GRAD_ACC_BATCH_SIZE": 8,
    "BATCH_SIZE": 8,
}

ROBERTA_CLASSIFIER_MINI_MOD = {
    "LEARNING_RATE": 2e-5,
    "DROPOUT": 0.1,
    "ENCODER": "CLS",
    "NUM_FEEDFORWARD_LAYERS": 1,
    "FEEDFORWARD_WIDTH_MULTIPLIER": 1,
    "EMBEDDING": "ROBERTA",
    "NUM_EPOCHS": 10,
    "PATIENCE": 3,
    "LR_SCHEDULE": 0,
    "GRAD_ACC_BATCH_SIZE": 16,
    "BATCH_SIZE": 8,
}

ROBERTA_CLASSIFIER_BIG = {
    "LEARNING_RATE": 2e-5,
    "DROPOUT": 0.1,
    "ENCODER": "CLS",
    "NUM_FEEDFORWARD_LAYERS": 1,
    "FEEDFORWARD_WIDTH_MULTIPLIER": 1,
    "EMBEDDING": "ROBERTA",
    "NUM_EPOCHS": 3,
    "PATIENCE": 3,
    "LR_SCHEDULE": 1,
    "GRAD_ACC_BATCH_SIZE": 16,
    "BATCH_SIZE": 16,
}

HYPERPARAMETERS = {
    "ROBERTA_CLASSIFIER_SMALL": ROBERTA_CLASSIFIER_SMALL,
    "ROBERTA_CLASSIFIER_MINI": ROBERTA_CLASSIFIER_MINI,
    "ROBERTA_CLASSIFIER_MINI_MOD": ROBERTA_CLASSIFIER_MINI_MOD,
    "ROBERTA_CLASSIFIER_BIG": ROBERTA_CLASSIFIER_BIG
}

Writing environments/hyperparameters.py


In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file hyptrain.txt \
                --line_by_line \
                --output_dir roberta_tapt4 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 32  \
                --model_name_or_path roberta-base \
                --eval_data_file hypdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  18% 12/65 [00:03<00:17,  3.00it/s]
Iteration:  20% 13/65 [00:04<00:17,  3.01it/s]
Iteration:  22% 14/65 [00:04<00:16,  3.00it/s]
Iteration:  23% 15/65 [00:04<00:16,  3.00it/s]
Iteration:  25% 16/65 [00:05<00:16,  3.00it/s]
Iteration:  26% 17/65 [00:05<00:15,  3.00it/s]
Iteration:  28% 18/65 [00:05<00:15,  3.00it/s]
Iteration:  29% 19/65 [00:06<00:15,  3.00it/s]
Iteration:  31% 20/65 [00:06<00:15,  3.00it/s]
Iteration:  32% 21/65 [00:07<00:14,  2.99it/s]
Iteration:  34% 22/65 [00:07<00:14,  3.00it/s]
Iteration:  35% 23/65 [00:07<00:14,  3.00it/s]
Iteration:  37% 24/65 [00:07<00:13,  3.00it/s]
Iteration:  38% 25/65 [00:08<00:13,  3.00it/s]
Iteration:  40% 26/65 [00:08<00:13,  3.00it/s]
Iteration:  42% 27/65 [00:08<00:12,  3.00it/s]
Iteration:  43% 28/65 [00:09<00:12,  3.00it/s]
Iteration:  45% 29/65 [00:09<00:12,  2.99it/s]
Iteration:  46% 30/65 [00:10<00:11,  2.99it/s]
Iteration:  48% 31/65 [00:10<00:11,  2.99it/s]
Iteration

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/hyp_tapt_04 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset hyperpartisan_news \
        --model roberta_tapt4 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-12 13:50:50,748 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 13:50:51,559 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 13:50:51,562 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 13:50:52,138 - INFO - allennlp.common.params - random_seed = 736117
2020-11-12 13:50:52,139 - INFO - allennlp.common.params - numpy_seed = 736117
2020-11-12 13:50:52,139 - INFO - allennlp.common.params - pytorch_seed = 736117
2020-11-12 13:50:52,146 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-12 13:50:52,148 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-12 13:50:52,148 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file chemtrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_chem_03 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 32  \
                --model_name_or_path roberta-base \
                --eval_data_file chemdev.txt \
                --do_eval \
                --evaluate_during_training  \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  97% 507/522 [00:48<00:01, 13.68it/s]
Iteration:  98% 509/522 [00:48<00:00, 13.81it/s]
Iteration:  98% 511/522 [00:49<00:00, 12.41it/s]
Iteration:  98% 513/522 [00:49<00:00, 12.17it/s]
Iteration:  99% 515/522 [00:49<00:00, 12.91it/s]
Iteration:  99% 517/522 [00:49<00:00, 13.07it/s]
Iteration:  99% 519/522 [00:49<00:00, 12.54it/s]
Iteration: 100% 522/522 [00:49<00:00, 10.48it/s]
Epoch:  85% 85/100 [1:02:19<11:09, 44.65s/it]
Iteration:   0% 0/522 [00:00<?, ?it/s]
Iteration:   0% 2/522 [00:00<00:30, 16.86it/s]
Iteration:   1% 4/522 [00:00<00:31, 16.41it/s]
Iteration:   1% 6/522 [00:00<00:33, 15.22it/s]
Iteration:   2% 8/522 [00:00<00:35, 14.47it/s]
Iteration:   2% 10/522 [00:00<00:35, 14.51it/s]
Iteration:   2% 12/522 [00:00<00:35, 14.34it/s]
Iteration:   3% 14/522 [00:00<00:36, 13.78it/s]
Iteration:   3% 16/522 [00:01<00:39, 12.76it/s]
Iteration:   3% 18/522 [00:01<00:37, 13.46it/s]
Iteration:   4% 20/522 [00:01<00:37, 13.43it

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/chem_tapt_03 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset chemprot \
        --model roberta_tapt_chem_03 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-12 16:04:34,025 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 16:04:34,763 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 16:04:34,772 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 16:04:35,460 - INFO - allennlp.common.params - random_seed = 324395
2020-11-12 16:04:35,460 - INFO - allennlp.common.params - numpy_seed = 324395
2020-11-12 16:04:35,460 - INFO - allennlp.common.params - pytorch_seed = 324395
2020-11-12 16:04:35,469 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-12 16:04:35,470 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-12 16:04:35,470 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file cittrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_cit_03 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 32  \
                --model_name_or_path roberta-base \
                --eval_data_file citdev.txt \
                --do_eval \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:   6% 12/211 [00:00<00:12, 15.49it/s]
Iteration:   7% 14/211 [00:00<00:13, 15.12it/s]
Iteration:   8% 16/211 [00:01<00:13, 14.76it/s]
Iteration:   9% 18/211 [00:01<00:12, 15.36it/s]
Iteration:   9% 20/211 [00:01<00:12, 15.15it/s]
Iteration:  10% 22/211 [00:01<00:12, 14.94it/s]
Iteration:  11% 24/211 [00:01<00:12, 14.50it/s]
Iteration:  12% 26/211 [00:01<00:11, 15.70it/s]
Iteration:  13% 28/211 [00:01<00:11, 15.69it/s]
Iteration:  14% 30/211 [00:01<00:11, 16.05it/s]
Iteration:  15% 32/211 [00:02<00:13, 13.65it/s]
Iteration:  16% 34/211 [00:02<00:14, 12.58it/s]
Iteration:  17% 36/211 [00:02<00:13, 13.00it/s]
Iteration:  18% 38/211 [00:02<00:13, 12.92it/s]
Iteration:  19% 40/211 [00:02<00:12, 13.88it/s]
Iteration:  20% 42/211 [00:02<00:11, 14.82it/s]
Iteration:  21% 44/211 [00:02<00:10, 15.54it/s]
Iteration:  22% 46/211 [00:03<00:10, 15.03it/s]
Iteration:  23% 49/211 [00:03<00:09, 16.24it/s]
Iteration:  24% 51/211 [00:03<00:10, 

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/cit_tapt_03 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset citation_intent \
        --model roberta_tapt_cit_03 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-12 16:50:40,177 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 16:50:40,606 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 16:50:40,608 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-12 16:50:41,063 - INFO - allennlp.common.params - random_seed = 292989
2020-11-12 16:50:41,063 - INFO - allennlp.common.params - numpy_seed = 292989
2020-11-12 16:50:41,063 - INFO - allennlp.common.params - pytorch_seed = 292989
2020-11-12 16:50:41,070 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-12 16:50:41,071 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-12 16:50:41,071 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [6]:
import json
import pandas as pd
!curl -Lo sciietrain.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/sciie/train.jsonl
!curl -Lo sciiedev.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/sciie/dev.jsonl
!curl -Lo sciieest.jsonl https://allennlp.s3-us-west-2.amazonaws.com/dont_stop_pretraining/data/sciie/test.jsonl
data = []
with open("sciietrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("sciietrain.txt", header=False, index=False)
data = []
with open("sciiedev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("sciiedev.txt", header=False, index=False)

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  804k  100  804k    0     0   478k      0  0:00:01  0:00:01 --:--:--  478k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  115k  100  115k    0     0  96301      0  0:00:01  0:00:01 --:--:-- 96222
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  243k  100  243k    0     0   175k      0  0:00:01  0:00:01 --:--:--  175k


In [7]:
!python -m scripts.run_language_modeling \
                --train_data_file sciietrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_sciie_06 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 32  \
                --model_name_or_path roberta-base \
                --eval_data_file sciiedev.txt \
                --do_eval \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 50

Streaming output truncated to the last 5000 lines.
Iteration:  57% 228/403 [00:12<00:09, 17.73it/s]
Iteration:  57% 230/403 [00:13<00:10, 16.69it/s]
Iteration:  58% 232/403 [00:13<00:09, 17.38it/s]
Iteration:  58% 234/403 [00:13<00:09, 17.92it/s]
Iteration:  59% 236/403 [00:13<00:09, 18.15it/s]
Iteration:  59% 238/403 [00:13<00:08, 18.59it/s]
Iteration:  60% 240/403 [00:13<00:08, 18.55it/s]
Iteration:  60% 242/403 [00:13<00:08, 18.71it/s]
Iteration:  61% 244/403 [00:13<00:08, 18.29it/s]
Iteration:  61% 246/403 [00:13<00:08, 18.76it/s]
Iteration:  62% 249/403 [00:14<00:07, 19.45it/s]
Iteration:  62% 251/403 [00:14<00:08, 18.86it/s]
Iteration:  63% 253/403 [00:14<00:08, 17.32it/s]
Iteration:  63% 255/403 [00:14<00:08, 16.97it/s]
Iteration:  64% 257/403 [00:14<00:09, 15.72it/s]
Iteration:  64% 259/403 [00:14<00:08, 16.65it/s]
Iteration:  65% 261/403 [00:14<00:08, 17.01it/s]
Iteration:  65% 263/403 [00:14<00:09, 15.38it/s]
Iteration:  66% 265/403 [00:15<00:08, 16.18it/s]
Iteration:  66% 26

In [8]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/sciie_tapt_06 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset sciie \
        --model roberta_tapt_sciie_06 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 00:20:25,709 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 00:20:26,549 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 00:20:26,552 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 00:20:27,159 - INFO - allennlp.common.params - random_seed = 266159
2020-11-13 00:20:27,160 - INFO - allennlp.common.params - numpy_seed = 266159
2020-11-13 00:20:27,160 - INFO - allennlp.common.params - pytorch_seed = 266159
2020-11-13 00:20:27,167 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 00:20:27,168 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 00:20:27,168 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [9]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/sciie_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset sciie \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 01:22:09,698 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:22:10,170 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:22:10,173 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:22:10,666 - INFO - allennlp.common.params - random_seed = 768107
2020-11-13 01:22:10,666 - INFO - allennlp.common.params - numpy_seed = 768107
2020-11-13 01:22:10,666 - INFO - allennlp.common.params - pytorch_seed = 768107
2020-11-13 01:22:10,674 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 01:22:10,675 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 01:22:10,675 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [10]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/citation_intent_nas_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset citation_intent \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 01:34:52,689 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:34:53,261 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:34:53,265 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:34:53,767 - INFO - allennlp.common.params - random_seed = 440596
2020-11-13 01:34:53,767 - INFO - allennlp.common.params - numpy_seed = 440596
2020-11-13 01:34:53,767 - INFO - allennlp.common.params - pytorch_seed = 440596
2020-11-13 01:34:53,775 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 01:34:53,777 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 01:34:53,777 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [11]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/chemprot_nas_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset chemprot \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 01:38:42,709 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:38:43,180 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:38:43,184 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:38:43,688 - INFO - allennlp.common.params - random_seed = 888584
2020-11-13 01:38:43,689 - INFO - allennlp.common.params - numpy_seed = 888584
2020-11-13 01:38:43,689 - INFO - allennlp.common.params - pytorch_seed = 888584
2020-11-13 01:38:43,696 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 01:38:43,698 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 01:38:43,698 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [12]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/rct20k_nas_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset rct-20k \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 01:51:08,195 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:51:08,805 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:51:08,808 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 01:51:09,336 - INFO - allennlp.common.params - random_seed = 358623
2020-11-13 01:51:09,336 - INFO - allennlp.common.params - numpy_seed = 358623
2020-11-13 01:51:09,336 - INFO - allennlp.common.params - pytorch_seed = 358623
2020-11-13 01:51:09,344 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 01:51:09,346 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 01:51:09,346 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [13]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/ag_nas_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset ag \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 05:37:45,954 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 05:37:46,441 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 05:37:46,444 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 05:37:46,980 - INFO - allennlp.common.params - random_seed = 648183
2020-11-13 05:37:46,980 - INFO - allennlp.common.params - numpy_seed = 648183
2020-11-13 05:37:46,980 - INFO - allennlp.common.params - pytorch_seed = 648183
2020-11-13 05:37:46,988 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 05:37:46,989 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 05:37:46,989 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [14]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/hyperpartisan_news_nas_01 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset hyperpartisan_news \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 08:20:54,267 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 08:20:54,714 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 08:20:54,717 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 08:20:55,182 - INFO - allennlp.common.params - random_seed = 397076
2020-11-13 08:20:55,182 - INFO - allennlp.common.params - numpy_seed = 397076
2020-11-13 08:20:55,182 - INFO - allennlp.common.params - pytorch_seed = 397076
2020-11-13 08:20:55,190 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 08:20:55,191 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 08:20:55,191 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [15]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/amazon_nas_03 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset amazon \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 08:24:21,009 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 08:24:21,455 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 08:24:21,459 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 08:24:21,931 - INFO - allennlp.common.params - random_seed = 576875
2020-11-13 08:24:21,932 - INFO - allennlp.common.params - numpy_seed = 576875
2020-11-13 08:24:21,932 - INFO - allennlp.common.params - pytorch_seed = 576875
2020-11-13 08:24:21,939 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 08:24:21,941 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 08:24:21,941 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [6]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/imdb_nas_03 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset imdb \
        --model roberta-base \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test

2020-11-13 14:16:11,558 - INFO - pytorch_pretrained_bert.modeling - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 14:16:12,854 - INFO - pytorch_transformers.modeling_bert - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 14:16:12,857 - INFO - pytorch_transformers.modeling_xlnet - Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
2020-11-13 14:16:13,481 - INFO - allennlp.common.params - random_seed = 469401
2020-11-13 14:16:13,481 - INFO - allennlp.common.params - numpy_seed = 469401
2020-11-13 14:16:13,481 - INFO - allennlp.common.params - pytorch_seed = 469401
2020-11-13 14:16:13,491 - INFO - allennlp.common.checks - Pytorch version: 1.7.0+cu101
2020-11-13 14:16:13,492 - INFO - allennlp.common.params - evaluate_on_test = True
2020-11-13 14:16:13,493 - INFO - allennlp.common.from_params - instantiating class <class 'allennlp.data.dataset

In [10]:
import json
import pandas as pd
data = []
with open("imdbtrain.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("imdbtrain.txt", header=False, index=False)
data = []
with open("imdbdev.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
       data.append(json.loads(line))
df = pd.DataFrame(data)
df.text.to_csv("imdbdev.txt", header=False, index=False)

In [ ]:
!python -m scripts.run_language_modeling \
                --train_data_file imdbtrain.txt \
                --line_by_line \
                --output_dir roberta_tapt_imdb_02 \
                --model_type roberta-base \
                --tokenizer_name roberta-base \
                --mlm \
                --per_gpu_train_batch_size 8 \
                --gradient_accumulation_steps 32  \
                --model_name_or_path roberta-base \
                --do_train \
                --num_train_epochs 100  \
                --learning_rate 0.0001 \
                --logging_steps 1000

2020-11-14 02:03:14.118287: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
11/14/2020 02:03:15 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 1, distributed training: False, 16-bits training: False
11/14/2020 02:03:16 - INFO - transformers.configuration_utils -   loading configuration file https://s3.amazonaws.com/models.huggingface.co/bert/roberta-base-config.json from cache at /root/.cache/torch/transformers/e1a2a406b5a05063c31f4dfdee7608986ba7c6393f7f79db5e69dcd197208534.117c81977c5979de8c088352e74ec6e70f5c66096c28b61d3c50101609b39690
11/14/2020 02:03:16 - INFO - transformers.configuration_utils -   Model config RobertaConfig {
  "_num_labels": 2,
  "architectures": [
    "RobertaForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "early_stopping": false,
  "eos_token_id": 2,
  "finetuning_task": null,
  "hidden_act": "gelu",
  "hidden_dropout_pro

In [ ]:
!python -m scripts.train \
        --config training_config/classifier.jsonnet \
        --serialization_dir model_logs/imdb_nas_03 \
        --hyperparameters ROBERTA_CLASSIFIER_MINI_MOD \
        --dataset imdb \
        --model roberta_tapt_imdb_02 \
        --device 0 \
        --perf +f1 \
        --evaluate_on_test